# Comparação de gêneros no OBRAS entre PALAVRAS e UDPIPE

## 1. Tratando corpoPALAVRAS e corpoOBRAS

In [ ]:
! wget https://www.linguateca.pt/acesso/corpos/obras/corpoPALAVRAS.gz
! wget https://www.linguateca.pt/acesso/corpos/obras/corpoOBRAS.gz

In [ ]:
! gunzip -f corpoPALAVRAS.gz
! gunzip -f corpoOBRAS.gz

In [ ]:
import re

In [ ]:
with open("corpoPALAVRAS", encoding="latin-1") as f:
    PALAVRAS = f.read()
    
with open("corpoOBRAS", encoding="latin-1") as f:
    OBRAS = f.read()

### 1.1 Criando estrutura de dados

In [ ]:
PALAVRAS_obras = [{
        'obra': re.findall('<obra id="([^"]*)"', x)[0],
        'tituloobra': re.findall('<tituloobra id="([^"]*)"', x)[0],
        'autor': re.findall('<autor id="([^"]*)"', x)[0],
        'sentences': [[{
                    'forma': z.split("\t")[0],
                    'lema': z.split("\t")[1],
                    'pos': z.split("\t")[2],
                    'genero': z.split("\t")[5]
                } for z in y.split("\n") if len(z.split("\t")) > 5
                      ] for y in re.findall('<u>(.*?)</u>', x, flags=re.DOTALL) if '\t' in y]
        } for x in re.findall('<obra .*?</obra>', PALAVRAS, flags=re.DOTALL)]

print(PALAVRAS_obras[0]['autor'])
print(PALAVRAS_obras[0]['obra'])
print(PALAVRAS_obras[0]['tituloobra'])
PALAVRAS_obras[0]['sentences'][0]

In [ ]:
OBRAS_obras = [{
        'obra': re.findall('<obra id="([^"]*)"', x)[0],
        'tituloobra': re.findall('<tituloobra id="([^"]*)"', x)[0],
        'autor': re.findall('<autor id="([^"]*)"', x)[0],
        'sentences': [[{
                    'forma': z.split("\t")[0],
                    'lema': z.split("\t")[8],
                    'pos': z.split("\t")[9],
                    'genero': z.split("\t")[12],
                    'sema': z.split("\t")[15]
                } for z in y.split("\n") if len(z.split("\t")) > 5
                      ] for y in re.findall('<u>(.*?)</u>', x, flags=re.DOTALL) if '\t' in y]
        } for x in re.findall('<obra .*?</obra>', OBRAS, flags=re.DOTALL)]

print(OBRAS_obras[0]['autor'])
print(OBRAS_obras[0]['obra'])
print(OBRAS_obras[0]['tituloobra'])
OBRAS_obras[0]['sentences'][0]

### 1.2 Alinhando PALAVRAS e OBRAS

#### Número de obras no PALAVRAS e no OBRAS

In [ ]:
print(len(PALAVRAS_obras))
print(len(OBRAS_obras))

#### Buscar obras que existem em um e não no outro

In [ ]:
obras_proibidas = [x for x in [y['tituloobra'] for y in PALAVRAS_obras] if x not in [z['tituloobra'] for z in OBRAS_obras]]
obras_proibidas += [x for x in [y['tituloobra'] for y in OBRAS_obras] if x not in [z['tituloobra'] for z in PALAVRAS_obras]]
print([x for x in [y['tituloobra'] for y in PALAVRAS_obras] if x not in [z['tituloobra'] for z in OBRAS_obras]])
print([x for x in [y['tituloobra'] for y in OBRAS_obras] if x not in [z['tituloobra'] for z in PALAVRAS_obras]])
PALAVRAS_obras = [x for x in PALAVRAS_obras if x['tituloobra'] not in obras_proibidas]
OBRAS_obras = [x for x in OBRAS_obras if x['tituloobra'] not in obras_proibidas]

print(len(PALAVRAS_obras))
print(len(OBRAS_obras))

#### Buscar obras fora de ordem entre PALAVRAS e OBRAS

In [ ]:
fora_de_ordem = False
for i in range(len(PALAVRAS_obras)):
    if PALAVRAS_obras[i]['tituloobra'] != OBRAS_obras[i]['tituloobra']:
        fora_de_ordem = True
        print(f"{PALAVRAS_obras[i]['tituloobra']} / {OBRAS_obras[i]['tituloobra']}")
        
if not fora_de_ordem:
    print("Não há obras fora de ordem")

#### Buscar obras sem id

In [ ]:
obras_proibidas = []
for obra in PALAVRAS_obras:
    if not obra['obra']:
        print(obra['tituloobra'])
        obras_proibidas.append(obra['tituloobra'])
        
for obra in OBRAS_obras:
    if not obra['obra']:
        print(obra['tituloobra'])
        obras_proibidas.append(obra['tituloobra']) 

PALAVRAS_obras = [x for x in PALAVRAS_obras if x['tituloobra'] not in obras_proibidas]
OBRAS_obras = [x for x in OBRAS_obras if x['tituloobra'] not in obras_proibidas]

print(len(PALAVRAS_obras))
print(len(OBRAS_obras))

#### Buscar obras sem sentença

In [ ]:
obras_proibidas = []
for obra in PALAVRAS_obras:
    if not obra['sentences']:
        print(obra['tituloobra'])
        if not obra['tituloobra'] in obras_proibidas:
            obras_proibidas.append(obra['tituloobra'])
        
for obra in OBRAS_obras:
    if not obra['sentences']:
        print(obra['tituloobra'])
        if not obra['tituloobra'] in obras_proibidas:
            obras_proibidas.append(obra['tituloobra'])

PALAVRAS_obras = [x for x in PALAVRAS_obras if x['tituloobra'] not in obras_proibidas]
OBRAS_obras = [x for x in OBRAS_obras if x['tituloobra'] not in obras_proibidas]

print("")
print(f"{len(obras_proibidas)} obras foram descartadas")
print(len(PALAVRAS_obras))
print(len(OBRAS_obras))

#### Buscar obras com número de sentenças diferente

In [ ]:
sentencas_diferentes = False
for i in range(len(PALAVRAS_obras)):
    if len(PALAVRAS_obras[i]['sentences']) != len(OBRAS_obras[i]['sentences']):
        sentencas_diferentes = True
        print(f"{i} - {PALAVRAS_obras[i]['tituloobra']}")
        print(f"PALAVRAS ({len(PALAVRAS_obras[i]['sentences'])}) / ACDC ({len(OBRAS_obras[i]['sentences'])})")
        
if not sentencas_diferentes:
    print('Não há obras com número de sentenças diferente')

#### Buscar sentenças com números de tokens diferentes e eliminar

In [ ]:
output = ""
sentences_inequal = {}
diff_list = {'OBRAS': {}, 'PALAVRAS': {}}

for i in range(len(OBRAS_obras)):
    sentences_inequal[i] = []
    for k in range(len(OBRAS_obras[i]['sentences'])):
        text_PALAVRAS = " ".join([x['forma'] for x in PALAVRAS_obras[i]['sentences'][k]])
        text_OBRAS = " ".join([x['forma'] for x in OBRAS_obras[i]['sentences'][k]])
        if len(text_PALAVRAS.split()) != len(text_OBRAS.split()):
            output += f"{i}-{k}:"
            output += "\n" + text_PALAVRAS
            output += "\n" + text_OBRAS
            output += "\n\n"
            lista_PALAVRAS = [x['forma'] for x in PALAVRAS_obras[i]['sentences'][k]]
            lista_OBRAS = [x['forma'] for x in OBRAS_obras[i]['sentences'][k]]
            for diff in lista_PALAVRAS:
                if diff not in lista_OBRAS:
                    diff_list['OBRAS'][diff] = diff_list['OBRAS'][diff] + 1 if diff in diff_list['OBRAS'] else 1
            for diff in lista_OBRAS:
                if diff not in lista_PALAVRAS:
                    diff_list['PALAVRAS'][diff] = diff_list['PALAVRAS'][diff] + 1 if diff in diff_list['PALAVRAS'] else 1
            sentences_inequal[i].append(k)

numero_sentences_pre = sum([len(x['sentences']) for x in OBRAS_obras])
print(f"Total de sentenças no corpus: {numero_sentences_pre}")
for i in range(len(PALAVRAS_obras)):
    PALAVRAS_obras[i]['sentences'] = [x for k, x in enumerate(PALAVRAS_obras[i]['sentences']) if k not in sentences_inequal[i]]
    OBRAS_obras[i]['sentences'] = [x for k, x in enumerate(OBRAS_obras[i]['sentences']) if k not in sentences_inequal[i]]
numero_sentences_pos = sum([len(x['sentences']) for x in OBRAS_obras])
print(f"Sentenças com tamanho diferente, que foram suprimidas do experimento (salvas em lista_suprimidas.txt): {numero_sentences_pre - numero_sentences_pos}")
print(f"Total de sentenças no corpus sem as suprimidas: {numero_sentences_pos}")

import pprint
for corpus in diff_list:
    print(f"\n{len(diff_list[corpus])} palavras que foram suprimidas de {corpus}\n")
    pprint.pprint(sorted(diff_list[corpus].items(), key=lambda x: x[1], reverse=True))
print(f"\n{output}")
with open("lista_suprimidas.txt", "w") as f:
    f.write(output)

### 1.3 Remover OBras que não foram tocadas

Coelho Neto (autor)
Raul Pompéia, 14 de julho na roça
tudo do Gregório de Matos, Alvarenga Peixoto, Basílio da Gama, Cláudio
Manuel da Costa, Tomás António Gonzaga, (estes podes obter através de
escola="barroco|arcadismo")
Adolfo Caminha, o Bom Crioulo
Júlio Ribeiro, A Carne
Aluísio Azevedo, O Homem
Aluísio Azevedo, O Coruja
Joaquim Manuel de Macedo, Os dois amores

In [ ]:
for o, obra in enumerate(OBRAS_obras):
    if obra['autor'] == 'Cosme Velho' and obra['tituloobra'] == 'Miss Kate':
        mark = o
        break
OBRAS_obras = [x for o, x in enumerate(OBRAS_obras) if o < mark]
PALAVRAS_obras = [x for o, x in enumerate(PALAVRAS_obras) if o < mark]
print(len(PALAVRAS_obras))
print(len(OBRAS_obras))

In [ ]:
print(len(PALAVRAS_obras))
print(len(OBRAS_obras))
PALAVRAS_obras = [x for x in PALAVRAS_obras if x['autor'].strip() not in ["Gregório de Matos", "Coelho Neto", "Alvarenga Peixoto", "Basílio da Gama", "Cláudio Manuel da Costa", "Tomás António Gonzaga"] and x['tituloobra'].lower().strip() not in ["o bom crioulo", "14 de julho na roça", "a carne", "o homem", "o coruja", "os dois amores"]]
OBRAS_obras = [x for x in OBRAS_obras if x['autor'].strip() not in ["Gregório de Matos", "Coelho Neto", "Alvarenga Peixoto", "Basílio da Gama", "Cláudio Manuel da Costa", "Tomás António Gonzaga"] and x['tituloobra'].lower().strip() not in ["o bom crioulo", "14 de julho na roça", "a carne", "o homem", "o coruja", "os dois amores"]]
print(len(PALAVRAS_obras))
print(len(OBRAS_obras))

### 1.4 Salvar PALAVRAS_obras e OBRAS_obras

In [ ]:
import pickle
with open("PALAVRAS_obras.p", "wb") as f:
    f.write(pickle.dumps(PALAVRAS_obras))
    
with open("OBRAS_obras.p", "wb") as f:
    f.write(pickle.dumps(OBRAS_obras))

### 1.5 Preparar material que será anotado pelo UDPipe

In [ ]:
import pickle
with open("PALAVRAS_obras.p", "rb") as f:
    PALAVRAS_obras = pickle.load(f)
    
with open("OBRAS_obras.p", "rb") as f:
    OBRAS_obras = pickle.load(f)

In [ ]:
count_x85 = 0
for i in range(len(OBRAS_obras)):
        for s in range(len(OBRAS_obras[i]['sentences'])):
            for t in range(len(OBRAS_obras[i]['sentences'][s])):
                if OBRAS_obras[i]['sentences'][s][t]['forma'] == "\x85":
                    OBRAS_obras[i]['sentences'][s][t]['forma'] = OBRAS_obras[i]['sentences'][s][t]['forma'].replace("\x85", "__INDEF__")
                    count_x85 += 1
                    
print(f"{count_x85} caracteres especiais no arquivo foram substituidos por __INDEF__")

In [ ]:
conllu = ""
for i in range(len(OBRAS_obras)):
    for s in range(len(OBRAS_obras[i]['sentences'])):
        conllu += "# sent_id = " + OBRAS_obras[i]['obra'].strip().replace(" ", "_") + ":" + str(i) + "-" + str(s)
        conllu += "\n# tituloobra = " + OBRAS_obras[i]['tituloobra']
        conllu += "\n# autor = " + OBRAS_obras[i]['autor']
        conllu += "\n# text = " + " ".join([x['forma'] for x in OBRAS_obras[i]['sentences'][s]])
        conllu += "\n" + "\n".join([x['forma'] + "\t" + "\t".join("_________") for x in OBRAS_obras[i]['sentences'][s]])
        conllu += "\n\n"

print("\n\n".join(conllu.split("\n\n")[:5]))
with open("corpoOBRAS_tokenizado.conllu", "w") as f:
    f.write(conllu)

## 2. Anotar com o UDPipe

In [ ]:
! python3 udpipe_vertical.py portuguese-bosque-ud-2.4-190531.udpipe corpoOBRAS_tokenizado.conllu corpoUDPIPE24r.conllu

In [ ]:
! rm corpoSTANZA.conllu.json

In [ ]:
! python3 ~/ACDC-UD/stanza_tokenized.py corpoOBRAS_tokenizado.conllu corpoSTANZA.conllu

### 2.1 Colocando gênero nos flat:name

In [ ]:
import estrutura_ud
ud24r = estrutura_ud.Corpus(recursivo=True)
ud24r.load('corpoUDPIPE24r.conllu')
changesUDPIPE24r = 0

for sentid, sentence in ud24r.sentences.items():
    if 'flat:name' in ud24r.sentences[sentid].to_str():
        for t, token in enumerate(sentence.tokens):
            if ud24r.sentences[sentid].tokens[t].deprel == "flat:name" and "Gender=" in ud24r.sentences[sentid].tokens[t].head_token.feats:
                ud24r.sentences[sentid].tokens[t].feats = ud24r.sentences[sentid].tokens[t].feats.split("|")
                ud24r.sentences[sentid].tokens[t].feats = [x for x in ud24r.sentences[sentid].tokens[t].feats if not x.startswith("Gender=")]
                ud24r.sentences[sentid].tokens[t].feats.append("Gender=" + ud24r.sentences[sentid].tokens[t].head_token.feats.split("Gender=")[1].split("|")[0])
                ud24r.sentences[sentid].tokens[t].feats = "|".join(sorted(ud24r.sentences[sentid].tokens[t].feats))
                changesUDPIPE24r += 1

print(f"\n{changesUDPIPE24r} modificações de flat:name foram realizadas no corpus UDPIPE24r")

In [ ]:
import estrutura_ud
stanza = estrutura_ud.Corpus(recursivo=True)
stanza.load('corpoSTANZA.conllu')
changesSTANZA = 0

for sentid, sentence in stanza.sentences.items():
    if 'flat:name' in stanza.sentences[sentid].to_str():
        for t, token in enumerate(sentence.tokens):
            if stanza.sentences[sentid].tokens[t].deprel == "flat:name" and "Gender=" in stanza.sentences[sentid].tokens[t].head_token.feats:
                stanza.sentences[sentid].tokens[t].feats = stanza.sentences[sentid].tokens[t].feats.split("|")
                stanza.sentences[sentid].tokens[t].feats = [x for x in stanza.sentences[sentid].tokens[t].feats if not x.startswith("Gender=")]
                stanza.sentences[sentid].tokens[t].feats.append("Gender=" + stanza.sentences[sentid].tokens[t].head_token.feats.split("Gender=")[1].split("|")[0])
                stanza.sentences[sentid].tokens[t].feats = "|".join(sorted(stanza.sentences[sentid].tokens[t].feats))
                changesSTANZA += 1

print(f"\n{changesSTANZA} modificações de flat:name foram realizadas no corpus STANZA")

### 2.2 Colocando flat:name no lema

In [ ]:
changesUDPIPE24r = 0

for sentid, sentence in ud24r.sentences.items():
    if 'flat:name' in ud24r.sentences[sentid].to_str():
        for t, token in enumerate(sentence.tokens):
            if ud24r.sentences[sentid].tokens[t].deprel == "flat:name":
                ud24r.sentences[sentid].tokens[t].head_token.lemma += "=" + ud24r.sentences[sentid].tokens[t].lemma
                changesUDPIPE24r += 1              
        for t, token in enumerate(sentence.tokens):
            if ud24r.sentences[sentid].tokens[t].deprel == "flat:name":
                ud24r.sentences[sentid].tokens[t].lemma = ud24r.sentences[sentid].tokens[t].head_token.lemma
                
print(f"\n{changesUDPIPE24r} modificações de lemma foram realizadas no corpus UDPIPE24r")

In [ ]:
changesSTANZA = 0

for sentid, sentence in stanza.sentences.items():
    if 'flat:name' in stanza.sentences[sentid].to_str():
        for t, token in enumerate(sentence.tokens):
            if stanza.sentences[sentid].tokens[t].deprel == "flat:name":
                stanza.sentences[sentid].tokens[t].head_token.lemma += "=" + stanza.sentences[sentid].tokens[t].lemma
                changesSTANZA += 1              
        for t, token in enumerate(sentence.tokens):
            if stanza.sentences[sentid].tokens[t].deprel == "flat:name":
                stanza.sentences[sentid].tokens[t].lemma = stanza.sentences[sentid].tokens[t].head_token.lemma
                
print(f"\n{changesSTANZA} modificações de lemma foram realizadas no corpus STANZA")

In [ ]:
ud24r.save('corpoUDPIPE24r_alterado.conllu')
stanza.save('corpoSTANZA_alterado.conllu')

## 3. Iniciar comparação > estrutura de dados das novas versões do corpus

In [1]:
import pickle
import re

with open("corpoUDPIPE24r_alterado.conllu") as f:
    UDPIPE24r = f.read()
print(UDPIPE24r.split("\n\n")[0])

with open("corpoSTANZA_alterado.conllu") as f:
    STANZA = f.read()
print(STANZA.split("\n\n")[0])

with open("PALAVRAS_obras.p", "rb") as f:
    PALAVRAS_obras = pickle.load(f)
    
with open("OBRAS_obras.p", "rb") as f:
    OBRAS_obras = pickle.load(f)

# text = A MORTALHA DE ALZIRA
# sent_id = A_Mortalha_de_Alzira_Prosa:romance_AA_1894_naturalismo_realismo_romantismo_masc:0-0
# autor = Aluísio Azevedo
# tituloobra = A Mortalha de Alzira
1	A	o	DET	_	Definite=Def|Gender=Fem|Number=Sing|PronType=Art	2	det	_	_
2	MORTALHA	MORTALHA=DE=ALZIRA	PROPN	_	Gender=Fem|Number=Sing	0	root	_	_
3	DE	MORTALHA=DE=ALZIRA	PROPN	_	Gender=Fem|Number=Sing	2	flat:name	_	_
4	ALZIRA	MORTALHA=DE=ALZIRA	PROPN	_	Gender=Fem|Number=Sing	2	flat:name	_	_
# text = A MORTALHA DE ALZIRA
# sent_id = A_Mortalha_de_Alzira_Prosa:romance_AA_1894_naturalismo_realismo_romantismo_masc:0-0
# tituloobra = A Mortalha de Alzira
# autor = Aluísio Azevedo
1	A	o	DET	_	Definite=Def|Gender=Fem|Number=Sing|PronType=Art	2	det	_	start_char=0|end_char=1
2	MORTALHA	mortalha	NOUN	_	Gender=Fem|Number=Sing	0	root	_	start_char=2|end_char=10
3	DE	de	ADP	_	_	4	case	_	start_char=11|end_char=13
4	ALZIRA	ALZIRA	PROPN	_	Number=Sing	2	nmod	_	start_char=14|end_char=20


In [2]:
OBRAS_obras[0]

{'obra': 'A_Mortalha_de_Alzira Prosa:romance AA 1894 naturalismo_realismo_romantismo masc ',
 'tituloobra': 'A Mortalha de Alzira',
 'autor': 'Aluísio Azevedo',
 'sentences': [[{'forma': 'A',
    'lema': 'o',
    'pos': 'DET_artd',
    'genero': 'F',
    'sema': '0'},
   {'forma': 'MORTALHA',
    'lema': 'mORTALHA',
    'pos': 'N',
    'genero': 'F',
    'sema': '0'},
   {'forma': 'DE', 'lema': 'de', 'pos': 'PRP', 'genero': '0', 'sema': '0'},
   {'forma': 'ALZIRA',
    'lema': 'Alzira',
    'pos': 'PROP',
    'genero': 'F',
    'sema': 'Pessoa'}],
  [{'forma': 'Aluísio',
    'lema': 'Aluísio=de=Azevedo',
    'pos': 'PROP',
    'genero': 'M',
    'sema': 'top'},
   {'forma': 'de',
    'lema': 'Aluísio=de=Azevedo',
    'pos': 'PROP',
    'genero': 'M',
    'sema': 'top'},
   {'forma': 'Azevedo',
    'lema': 'Aluísio=de=Azevedo',
    'pos': 'PROP',
    'genero': 'M',
    'sema': 'top'}],
  [{'forma': 'A', 'lema': 'o', 'pos': 'DET_artd', 'genero': 'F', 'sema': '0'},
   {'forma': 'cela', 'l

In [3]:
PALAVRAS_obras[0]

{'obra': 'A_Mortalha_de_Alzira Prosa:romance AA 1894 naturalismo_realismo_romantismo masc ',
 'tituloobra': 'A Mortalha de Alzira',
 'autor': 'Aluísio Azevedo',
 'sentences': [[{'forma': 'A', 'lema': 'o', 'pos': 'DET_artd', 'genero': 'F'},
   {'forma': 'MORTALHA', 'lema': 'mORTALHA', 'pos': 'N', 'genero': 'F'},
   {'forma': 'DE', 'lema': 'de', 'pos': 'PRP', 'genero': '0'},
   {'forma': 'ALZIRA', 'lema': 'Alzira', 'pos': 'PROP', 'genero': 'F'}],
  [{'forma': 'Aluísio',
    'lema': 'Aluísio=de=Azevedo',
    'pos': 'PROP',
    'genero': 'M'},
   {'forma': 'de', 'lema': 'Aluísio=de=Azevedo', 'pos': 'PROP', 'genero': 'M'},
   {'forma': 'Azevedo',
    'lema': 'Aluísio=de=Azevedo',
    'pos': 'PROP',
    'genero': 'M'}],
  [{'forma': 'A', 'lema': 'o', 'pos': 'DET_artd', 'genero': 'F'},
   {'forma': 'cela', 'lema': 'cela', 'pos': 'N', 'genero': 'F'},
   {'forma': 'misteriosa', 'lema': 'misterioso', 'pos': 'ADJ', 'genero': 'F'}],
  [{'forma': 'No', 'lema': 'em+o', 'pos': 'PRP+DET_artd', 'genero

In [4]:
obras = {}
for obra in re.findall(r"# sent_id = .*:(.*?)-", UDPIPE24r):
    if not int(obra) in obras:
        obras[int(obra)] = {'sentences': []}

for sentence in UDPIPE24r.split("\n\n"):
    if sentence:
        obras[int(sentence.split("# sent_id = ")[1].split("\n")[0].rsplit(":", 1)[1].rsplit("-", 1)[0])]['obra'] = sentence.split("# sent_id = ")[1].split("\n")[0].rsplit(":", 1)[0]
        obras[int(sentence.split("# sent_id = ")[1].split("\n")[0].rsplit(":", 1)[1].rsplit("-", 1)[0])]['tituloobra'] = sentence.split("# tituloobra = ")[1].split("\n")[0]
        obras[int(sentence.split("# sent_id = ")[1].split("\n")[0].rsplit(":", 1)[1].rsplit("-", 1)[0])]['autor'] = sentence.split("# autor = ")[1].split("\n")[0]
        obras[int(sentence.split("# sent_id = ")[1].split("\n")[0].rsplit(":", 1)[1].rsplit("-", 1)[0])]['sentences'].append([{
                    'forma': z.split("\t")[1],
                    'lema': z.split("\t")[2],
                    'pos': z.split("\t")[3],
                    'genero': z.split("\t")[5].split("Gender=")[1].split("|")[0] if "Gender=" in z.split("\t")[5] else "0",
                } for z in sentence.splitlines() if len(z.split("\t")) > 5])

UDPIPE24r_obras = [{
        'obra': obras[x]['obra'],
        'tituloobra': obras[x]['tituloobra'],
        'autor': obras[x]['autor'],
        'sentences': obras[x]['sentences'],
    } for x in obras]

UDPIPE24r_obras[0]

{'obra': 'A_Mortalha_de_Alzira_Prosa:romance_AA_1894_naturalismo_realismo_romantismo_masc',
 'tituloobra': 'A Mortalha de Alzira',
 'autor': 'Aluísio Azevedo',
 'sentences': [[{'forma': 'A', 'lema': 'o', 'pos': 'DET', 'genero': 'Fem'},
   {'forma': 'MORTALHA',
    'lema': 'MORTALHA=DE=ALZIRA',
    'pos': 'PROPN',
    'genero': 'Fem'},
   {'forma': 'DE',
    'lema': 'MORTALHA=DE=ALZIRA',
    'pos': 'PROPN',
    'genero': 'Fem'},
   {'forma': 'ALZIRA',
    'lema': 'MORTALHA=DE=ALZIRA',
    'pos': 'PROPN',
    'genero': 'Fem'}],
  [{'forma': 'Aluísio', 'lema': 'Aluísio', 'pos': 'PROPN', 'genero': 'Masc'},
   {'forma': 'de', 'lema': 'de', 'pos': 'ADP', 'genero': '0'},
   {'forma': 'Azevedo', 'lema': 'Azevedo', 'pos': 'PROPN', 'genero': '0'}],
  [{'forma': 'A', 'lema': 'o', 'pos': 'DET', 'genero': 'Fem'},
   {'forma': 'cela', 'lema': 'cela', 'pos': 'NOUN', 'genero': 'Fem'},
   {'forma': 'misteriosa',
    'lema': 'misterioso',
    'pos': 'ADJ',
    'genero': 'Fem'}],
  [{'forma': 'No', 'lema

In [5]:
obras = {}
for obra in re.findall(r"# sent_id = .*:(.*?)-", STANZA):
    if not int(obra) in obras:
        obras[int(obra)] = {'sentences': []}

for sentence in STANZA.split("\n\n"):
    if sentence:
        obras[int(sentence.split("# sent_id = ")[1].split("\n")[0].rsplit(":", 1)[1].rsplit("-", 1)[0])]['obra'] = sentence.split("# sent_id = ")[1].split("\n")[0].rsplit(":", 1)[0]
        obras[int(sentence.split("# sent_id = ")[1].split("\n")[0].rsplit(":", 1)[1].rsplit("-", 1)[0])]['tituloobra'] = sentence.split("# tituloobra = ")[1].split("\n")[0]
        obras[int(sentence.split("# sent_id = ")[1].split("\n")[0].rsplit(":", 1)[1].rsplit("-", 1)[0])]['autor'] = sentence.split("# autor = ")[1].split("\n")[0]
        obras[int(sentence.split("# sent_id = ")[1].split("\n")[0].rsplit(":", 1)[1].rsplit("-", 1)[0])]['sentences'].append([{
                    'forma': z.split("\t")[1],
                    'lema': z.split("\t")[2],
                    'pos': z.split("\t")[3],
                    'genero': z.split("\t")[5].split("Gender=")[1].split("|")[0] if "Gender=" in z.split("\t")[5] else "0",
                } for z in sentence.splitlines() if len(z.split("\t")) > 5])

STANZA_obras = [{
        'obra': obras[x]['obra'],
        'tituloobra': obras[x]['tituloobra'],
        'autor': obras[x]['autor'],
        'sentences': obras[x]['sentences'],
    } for x in obras]

STANZA_obras[0]

{'obra': 'A_Mortalha_de_Alzira_Prosa:romance_AA_1894_naturalismo_realismo_romantismo_masc',
 'tituloobra': 'A Mortalha de Alzira',
 'autor': 'Aluísio Azevedo',
 'sentences': [[{'forma': 'A', 'lema': 'o', 'pos': 'DET', 'genero': 'Fem'},
   {'forma': 'MORTALHA', 'lema': 'mortalha', 'pos': 'NOUN', 'genero': 'Fem'},
   {'forma': 'DE', 'lema': 'de', 'pos': 'ADP', 'genero': '0'},
   {'forma': 'ALZIRA', 'lema': 'ALZIRA', 'pos': 'PROPN', 'genero': '0'}],
  [{'forma': 'Aluísio', 'lema': 'Aluísio', 'pos': 'PROPN', 'genero': 'Masc'},
   {'forma': 'de', 'lema': 'de', 'pos': 'ADP', 'genero': '0'},
   {'forma': 'Azevedo', 'lema': 'Azevedo', 'pos': 'PROPN', 'genero': '0'}],
  [{'forma': 'A', 'lema': 'o', 'pos': 'DET', 'genero': 'Fem'},
   {'forma': 'cela', 'lema': 'cela', 'pos': 'NOUN', 'genero': 'Fem'},
   {'forma': 'misteriosa',
    'lema': 'misterioso',
    'pos': 'ADJ',
    'genero': 'Fem'}],
  [{'forma': 'No', 'lema': 'no', 'pos': 'ADP', 'genero': '0'},
   {'forma': 'ano', 'lema': 'ano', 'pos': 

### 3.1 Comparar os corpora

In [6]:
print(len(PALAVRAS_obras))
print(len(OBRAS_obras))
print(len(UDPIPE24r_obras))
print(len(STANZA_obras))

sentencas_diferentes = False
for i in range(len(PALAVRAS_obras)):
    if len(PALAVRAS_obras[i]['sentences']) != len(OBRAS_obras[i]['sentences']) or \
    len(OBRAS_obras[i]['sentences']) != len(UDPIPE24r_obras[i]['sentences']) or \
    len(STANZA_obras[i]['sentences']) != len(OBRAS_obras[i]['sentences']):
        sentencas_diferentes = True
        print(f"{i} - {PALAVRAS_obras[i]['tituloobra']}")
        print(f"PALAVRAS ({len(PALAVRAS_obras[i]['sentences'])}) / ACDC ({len(OBRAS_obras[i]['sentences'])}) / UDPIPE24r ({len(UDPIPE24r_obras[i]['sentences'])}) / STANZA ({len(STANZA_obras[i]['sentences'])})")
        
if not sentencas_diferentes:
    print('Não há obras com número de sentenças diferente')

226
226
226
226
Não há obras com número de sentenças diferente


### 3.2 Normalizar as formas de dizer o gênero

In [7]:
lista_genero_PALAVRAS = []
lista_genero_OBRAS = []
lista_genero_UDPIPE24r = []
lista_genero_STANZA = []

generos_PALAVRAS = [c['genero'] for a in PALAVRAS_obras for b in a['sentences'] for c in b]
[lista_genero_PALAVRAS.append(x) for x in generos_PALAVRAS if not x in lista_genero_PALAVRAS]
print(lista_genero_PALAVRAS)

generos_OBRAS = [c['genero'] for a in OBRAS_obras for b in a['sentences'] for c in b]
[lista_genero_OBRAS.append(x) for x in generos_OBRAS if not x in lista_genero_OBRAS]
print(lista_genero_OBRAS)

generos_UDPIPE24r = [c['genero'] for a in UDPIPE24r_obras for b in a['sentences'] for c in b]
[lista_genero_UDPIPE24r.append(x) for x in generos_UDPIPE24r if not x in lista_genero_UDPIPE24r]
print(lista_genero_UDPIPE24r)

generos_STANZA = [c['genero'] for a in STANZA_obras for b in a['sentences'] for c in b]
[lista_genero_STANZA.append(x) for x in generos_STANZA if not x in lista_genero_STANZA]
print(lista_genero_STANZA)

['F', '0', 'M', 'M/F', 'M/F+M', 'M+M/F', 'M/F+M/F', 'F+M/F', 'M/F+F', 'F+F', 'M+M', 'F_P_V_uninfl_INF', '3P', 'M_S_V_uninfl_INF', 'M/F_2S_DAT_PERS_M', 'M/F_3S/P_DAT_PERS_M', 'SUP', 'M/S', 'F+M', 'm', 'M/F_1S_DAT_PERS_F', 'M_1S_DAT_PERS_F', '3S', 'M/F_1S_DAT_PERS_M', '1S']
['F', '0', 'M', 'M/F', 'M/F+M', 'M+M/F', 'M/F+M/F', 'F+M/F', 'M/F+F', 'F+F', 'M+M', 'F_P_V_uninfl_INF', '3P', 'M_S_V_uninfl_INF', 'M/F_2S_DAT_PERS_M', 'M/F_3S/P_DAT_PERS_M', 'SUP', 'M/S', 'F+M', 'm', 'M/F_1S_DAT_PERS_F', 'M_1S_DAT_PERS_F', '3S', 'F"', 'M/F_1S_DAT_PERS_M', '1S']
['Fem', 'Masc', '0', 'Unsp']
['Fem', '0', 'Masc', 'Unsp']


In [8]:
mudanca_de_genero = {
    'F': 'F', 
    '0': '0', 
    'M': 'M', 
    'M/F': 'M/F', 
    'M/F+M': 'M', 
    '+F': 'F', 
    'M+M/F': 'M', 
    'M/F+M/F': 'M/F', 
    'F+M/F': 'F', 
    'M/F+F': 'F', 
    '+M': 'M', 
    'F+F': 'F', 
    'M/F+0': '0', 
    'M+M': 'M', 
    'SUP': 'SUP', 
    'F_P_V_uninfl_INF': 'F', 
    '3P': '3P', 
    '2S': '2S', 
    'M_S_V_uninfl_INF': 'M', 
    'M/F_2S_DAT_PERS_M': 'M/F', 
    'M/F_3S/P_DAT_PERS_M': 'M/F', 
    '+0': '0', 
    'M/S': 'M', 
    'F+M': 'F+M', 
    'm': 'M', 
    'M/F_1S_DAT_PERS_F': 'M/F', 
    'M_1S_DAT_PERS_F': 'M', 
    'M/F_1S_DAT_PERS_M': 'M/F',
    '3S': '3S', 
    'F"': 'F', 
    '1S': '1S', 
    'Fem': 'F',
    'Masc': 'M', 
    'Unsp': 'M/F'
}

for a in range(len(OBRAS_obras)):
    for b in range(len(OBRAS_obras[a]['sentences'])):
        for c in range(len(OBRAS_obras[a]['sentences'][b])):
            OBRAS_obras[a]['sentences'][b][c]['genero'] = mudanca_de_genero[OBRAS_obras[a]['sentences'][b][c]['genero']]
            PALAVRAS_obras[a]['sentences'][b][c]['genero'] = mudanca_de_genero[PALAVRAS_obras[a]['sentences'][b][c]['genero']]
            UDPIPE24r_obras[a]['sentences'][b][c]['genero'] = mudanca_de_genero[UDPIPE24r_obras[a]['sentences'][b][c]['genero']]
            STANZA_obras[a]['sentences'][b][c]['genero'] = mudanca_de_genero[STANZA_obras[a]['sentences'][b][c]['genero']]

lista_genero_OBRAS = []            
print('\nCom a operação de mudança de gênero:')
generos_OBRAS = [c['genero'] for a in OBRAS_obras for b in a['sentences'] for c in b]
[lista_genero_OBRAS.append(x) for x in generos_OBRAS if not x in lista_genero_OBRAS]
print(lista_genero_OBRAS)


Com a operação de mudança de gênero:
['F', '0', 'M', 'M/F', '3P', 'SUP', 'F+M', '3S', '1S']


In [9]:
generos_aceitaveis = ['F', '0', 'M', 'M/F']

### 3.3 Cálculos de comparação

#### Características da comparação

In [10]:
SEG_OBRAS = []
SEG_PALAVRAS = []
SEG_UDPIPE24r = []
SEG_STANZA = []
PROPN_OBRAS = []

for o, obra in enumerate(OBRAS_obras):
    for s, sentence in enumerate(obra['sentences']):
        for t, token in enumerate(sentence):
            if token['pos'] == "PROP" and token['genero'] in generos_aceitaveis:
                if (t == 0 or sentence[t-1]['lema'] != token['lema']):
                    PROPN_OBRAS.append(f"{o}<delimitador>{s}<delimitador>{t}<delimitador>{token['lema'].lower()}")
            if token['pos'] == "PROP" and token['genero'] in generos_aceitaveis and token['sema'] in ['Pessoa', "hum"]:
                if (t == 0 or sentence[t-1]['lema'] != token['lema']):
                    SEG_OBRAS.append(f"{o}<delimitador>{s}<delimitador>{t}<delimitador>{token['lema'].lower()}")

for o, obra in enumerate(PALAVRAS_obras):
    for s, sentence in enumerate(obra['sentences']):
        for t, token in enumerate(sentence):
            if token['pos'] == "PROP" and token['genero'] in generos_aceitaveis:
                if (t == 0 or sentence[t-1]['lema'] != token['lema']):
                    SEG_PALAVRAS.append(f"{o}<delimitador>{s}<delimitador>{t}<delimitador>{token['lema'].lower()}")

for o, obra in enumerate(UDPIPE24r_obras):
    for s, sentence in enumerate(obra['sentences']):
        for t, token in enumerate(sentence):
            if token['pos'] == "PROPN" and token['genero'] in generos_aceitaveis:
                if (t == 0 or sentence[t-1]['lema'] != token['lema']):
                    SEG_UDPIPE24r.append(f"{o}<delimitador>{s}<delimitador>{t}<delimitador>{token['lema'].lower()}")

for o, obra in enumerate(STANZA_obras):
    for s, sentence in enumerate(obra['sentences']):
        for t, token in enumerate(sentence):
            if token['pos'] == "PROPN" and token['genero'] in generos_aceitaveis:
                if (t == 0 or sentence[t-1]['lema'] != token['lema']):
                    SEG_STANZA.append(f"{o}<delimitador>{s}<delimitador>{t}<delimitador>{token['lema'].lower()}")


#### Acertos de nome próprio e segmentação em cada corpora

In [11]:
dicOBRAS_PROP = []
PALAVRAS_acertos_PROP = []
PALAVRAS_erros_PROP = 0
UDPIPE24r_acertos_PROP = []
UDPIPE24r_erros_PROP = 0
STANZA_acertos_PROP = []
STANZA_erros_PROP = 0

acerto_ambos = []
for seg in SEG_OBRAS:
    if seg in SEG_PALAVRAS and seg in SEG_UDPIPE24r and seg in SEG_STANZA:
        acerto_ambos.append(seg)
        
for seg in SEG_PALAVRAS:
    if seg in SEG_OBRAS:
        PALAVRAS_acertos_PROP.append(seg)
    else:
        PALAVRAS_erros_PROP += 1
        
for seg in SEG_UDPIPE24r:
    if seg in SEG_OBRAS:
        UDPIPE24r_acertos_PROP.append(seg)
    else:
        UDPIPE24r_erros_PROP += 1
        
for seg in SEG_STANZA:
    if seg in SEG_OBRAS:
        STANZA_acertos_PROP.append(seg)
    else:
        STANZA_erros_PROP += 1

#### Acertos de gênero

In [47]:
nomes_comparaveis_todos = len(acerto_ambos)
nomes_comparaveis_PALAVRAS = len(PALAVRAS_acertos_PROP)
nomes_comparaveis_UDPIPE24r = len(UDPIPE24r_acertos_PROP)
nomes_comparaveis_STANZA = len(STANZA_acertos_PROP)

acertoGenero_PALAVRAS = 0
acertoGenero_UDPIPE24r = 0
acertoGenero_STANZA = 0

acertoGenero_PALAVRAS_total = 0
acertoGenero_UDPIPE24r_total = 0
acertoGenero_STANZA_total = 0

errors_distribution = {}
for seg in SEG_OBRAS:
    o = int(seg.split("<delimitador>")[0])
    s = int(seg.split("<delimitador>")[1])
    t = int(seg.split("<delimitador>")[2])
    if seg in SEG_PALAVRAS:
        acertoGenero_PALAVRAS += 1 if OBRAS_obras[o]['sentences'][s][t]['genero'] == PALAVRAS_obras[o]['sentences'][s][t]['genero'] else 0
    if seg in SEG_UDPIPE24r:
        acertoGenero_UDPIPE24r += 1 if OBRAS_obras[o]['sentences'][s][t]['genero'] == UDPIPE24r_obras[o]['sentences'][s][t]['genero'] else 0
    if seg in SEG_STANZA:
        acertoGenero_STANZA += 1 if OBRAS_obras[o]['sentences'][s][t]['genero'] == STANZA_obras[o]['sentences'][s][t]['genero'] else 0
    quem_errou = []
    if seg in acerto_ambos:
        if OBRAS_obras[o]['sentences'][s][t]['genero'] == PALAVRAS_obras[o]['sentences'][s][t]['genero']:
            acertoGenero_PALAVRAS_total += 1
        else:
            quem_errou.append("PALAVRAS")
        if OBRAS_obras[o]['sentences'][s][t]['genero'] == UDPIPE24r_obras[o]['sentences'][s][t]['genero']:
            acertoGenero_UDPIPE24r_total += 1
        else:
            quem_errou.append("UDPIPE24r")
        if OBRAS_obras[o]['sentences'][s][t]['genero'] == STANZA_obras[o]['sentences'][s][t]['genero']:
            acertoGenero_STANZA_total += 1
        else:
            quem_errou.append("STANZA")
        
        if quem_errou:
            if not "|".join(quem_errou) in errors_distribution:
                errors_distribution["|".join(quem_errou)] = []
            errors_distribution["|".join(quem_errou)].append(seg)
        else:
            if not "NENHUM" in errors_distribution:
                errors_distribution["NENHUM"] = []
            errors_distribution["NENHUM"].append(seg)
print([x for x in errors_distribution])
errors_distribution

['UDPIPE24r', 'PALAVRAS|UDPIPE24r|STANZA', 'NENHUM', 'UDPIPE24r|STANZA', 'STANZA', 'PALAVRAS', 'PALAVRAS|STANZA', 'PALAVRAS|UDPIPE24r']


{'UDPIPE24r': ['0<delimitador>4<delimitador>44<delimitador>torré',
  '0<delimitador>302<delimitador>6<delimitador>alzira',
  '0<delimitador>303<delimitador>46<delimitador>alzira',
  '0<delimitador>315<delimitador>10<delimitador>margarida',
  '0<delimitador>320<delimitador>9<delimitador>gabriela',
  '0<delimitador>329<delimitador>12<delimitador>alzira',
  '0<delimitador>340<delimitador>8<delimitador>gabriela',
  '0<delimitador>370<delimitador>1<delimitador>gabriela',
  '0<delimitador>371<delimitador>0<delimitador>alzira',
  '0<delimitador>383<delimitador>19<delimitador>gabriela',
  '0<delimitador>393<delimitador>9<delimitador>gabriela',
  '0<delimitador>395<delimitador>6<delimitador>alzira',
  '0<delimitador>409<delimitador>0<delimitador>alzira',
  '0<delimitador>429<delimitador>1<delimitador>gabriela',
  '0<delimitador>442<delimitador>7<delimitador>alzira',
  '0<delimitador>450<delimitador>0<delimitador>alzira',
  '0<delimitador>465<delimitador>7<delimitador>gabriela',
  '0<delimitador

### N-grams

In [13]:
distribution_ngrams = {}
for nome in SEG_OBRAS:
    if not len(nome.split("<delimitador>")[3].split("=")) in distribution_ngrams:
        distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))] = {}
    if not 'OBRAS' in distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))]:
        distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))]['OBRAS'] = 0
    distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))]['OBRAS'] += 1
    
for nome in PALAVRAS_acertos_PROP:
    if not len(nome.split("<delimitador>")[3].split("=")) in distribution_ngrams:
        distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))] = {}
    if not 'PALAVRAS' in distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))]:
        distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))]['PALAVRAS'] = 0
    distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))]['PALAVRAS'] += 1
    
for nome in UDPIPE24r_acertos_PROP:
    if not len(nome.split("<delimitador>")[3].split("=")) in distribution_ngrams:
        distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))] = {}
    if not 'UDPIPE24r' in distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))]:
        distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))]['UDPIPE24r'] = 0
    distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))]['UDPIPE24r'] += 1
    
for nome in STANZA_acertos_PROP:
    if not len(nome.split("<delimitador>")[3].split("=")) in distribution_ngrams:
        distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))] = {}
    if not 'STANZA' in distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))]:
        distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))]['STANZA'] = 0
    distribution_ngrams[len(nome.split("<delimitador>")[3].split("="))]['STANZA'] += 1

print(distribution_ngrams)

{1: {'OBRAS': 63595, 'PALAVRAS': 63005, 'UDPIPE24r': 50253, 'STANZA': 57523}, 2: {'OBRAS': 13757, 'PALAVRAS': 13737, 'UDPIPE24r': 12502, 'STANZA': 13188}, 3: {'OBRAS': 2977, 'PALAVRAS': 2905, 'UDPIPE24r': 854, 'STANZA': 1244}, 4: {'OBRAS': 673, 'PALAVRAS': 658, 'UDPIPE24r': 81, 'STANZA': 112}, 6: {'OBRAS': 39, 'PALAVRAS': 39, 'UDPIPE24r': 1}, 5: {'OBRAS': 170, 'PALAVRAS': 165, 'UDPIPE24r': 16, 'STANZA': 12}, 7: {'OBRAS': 13, 'PALAVRAS': 12}, 9: {'OBRAS': 1, 'PALAVRAS': 1}, 8: {'OBRAS': 5, 'PALAVRAS': 4}}


### Lemas diferentes

In [30]:
lemas_diferentes = {}
for token in SEG_OBRAS:
    o = int(token.split("<delimitador>")[0])
    s = int(token.split("<delimitador>")[1])
    t = int(token.split("<delimitador>")[2])
    token = OBRAS_obras[o]['sentences'][s][t]
    if not token['genero'] in lemas_diferentes:
        lemas_diferentes[token['genero']] = {}
    if not 'OBRAS' in lemas_diferentes[token['genero']]:
        lemas_diferentes[token['genero']]['OBRAS'] = {}
    if not token['lema'] in lemas_diferentes[token['genero']]['OBRAS']:
        lemas_diferentes[token['genero']]['OBRAS'][token['lema']] = 0
    lemas_diferentes[token['genero']]['OBRAS'][token['lema']] += 1
        
for token in PALAVRAS_acertos_PROP:
    o = int(token.split("<delimitador>")[0])
    s = int(token.split("<delimitador>")[1])
    t = int(token.split("<delimitador>")[2])
    token = PALAVRAS_obras[o]['sentences'][s][t]
    if not token['genero'] in lemas_diferentes:
        lemas_diferentes[token['genero']] = {}
    if not 'PALAVRAS' in lemas_diferentes[token['genero']]:
        lemas_diferentes[token['genero']]['PALAVRAS'] = {}
    if not token['lema'] in lemas_diferentes[token['genero']]['PALAVRAS']:
        lemas_diferentes[token['genero']]['PALAVRAS'][token['lema']] = 0
    lemas_diferentes[token['genero']]['PALAVRAS'][token['lema']] += 1
        
for token in UDPIPE24r_acertos_PROP:
    o = int(token.split("<delimitador>")[0])
    s = int(token.split("<delimitador>")[1])
    t = int(token.split("<delimitador>")[2])
    token = UDPIPE24r_obras[o]['sentences'][s][t]
    if not token['genero'] in lemas_diferentes:
        lemas_diferentes[token['genero']] = {}
    if not 'UDPIPE24r' in lemas_diferentes[token['genero']]:
        lemas_diferentes[token['genero']]['UDPIPE24r'] = {}
    if not token['lema'] in lemas_diferentes[token['genero']]['UDPIPE24r']:
        lemas_diferentes[token['genero']]['UDPIPE24r'][token['lema']] = 0
    lemas_diferentes[token['genero']]['UDPIPE24r'][token['lema']] += 1
        
for token in STANZA_acertos_PROP:
    o = int(token.split("<delimitador>")[0])
    s = int(token.split("<delimitador>")[1])
    t = int(token.split("<delimitador>")[2])
    token = STANZA_obras[o]['sentences'][s][t]
    if not token['genero'] in lemas_diferentes:
        lemas_diferentes[token['genero']] = {}
    if not 'STANZA' in lemas_diferentes[token['genero']]:
        lemas_diferentes[token['genero']]['STANZA'] = {}
    if not token['lema'] in lemas_diferentes[token['genero']]['STANZA']:
        lemas_diferentes[token['genero']]['STANZA'][token['lema']] = 0
    lemas_diferentes[token['genero']]['STANZA'][token['lema']] += 1

In [39]:
analises_ambiguas = {}
for token in SEG_OBRAS:
    o = int(token.split("<delimitador>")[0])
    s = int(token.split("<delimitador>")[1])
    t = int(token.split("<delimitador>")[2])
    token = OBRAS_obras[o]['sentences'][s][t]
    diverge = -1
    onde = []
    for genero in lemas_diferentes:
        if 'OBRAS' in lemas_diferentes[genero] and token['lema'] in lemas_diferentes[genero]['OBRAS']:
            diverge += 1
            onde.append(genero)
    if diverge:
        if not 'OBRAS' in analises_ambiguas:
            analises_ambiguas['OBRAS'] = {}
        for _genero in onde:
            if not token['lema'] in analises_ambiguas['OBRAS']:
                analises_ambiguas['OBRAS'][token['lema']] = {}
            analises_ambiguas['OBRAS'][token['lema']][_genero] = lemas_diferentes[_genero]['OBRAS'][token['lema']]
            
for token in PALAVRAS_acertos_PROP:
    o = int(token.split("<delimitador>")[0])
    s = int(token.split("<delimitador>")[1])
    t = int(token.split("<delimitador>")[2])
    token = PALAVRAS_obras[o]['sentences'][s][t]
    diverge = -1
    onde = []
    for genero in lemas_diferentes:
        if 'PALAVRAS' in lemas_diferentes[genero] and token['lema'] in lemas_diferentes[genero]['PALAVRAS']:
            diverge += 1
            onde.append(genero)
    if diverge:
        if not 'PALAVRAS' in analises_ambiguas:
            analises_ambiguas['PALAVRAS'] = {}
        for _genero in onde:
            if not token['lema'] in analises_ambiguas['PALAVRAS']:
                analises_ambiguas['PALAVRAS'][token['lema']] = {}
            analises_ambiguas['PALAVRAS'][token['lema']][_genero] = lemas_diferentes[_genero]['PALAVRAS'][token['lema']]
            
for token in UDPIPE24r_acertos_PROP:
    o = int(token.split("<delimitador>")[0])
    s = int(token.split("<delimitador>")[1])
    t = int(token.split("<delimitador>")[2])
    token = UDPIPE24r_obras[o]['sentences'][s][t]
    diverge = -1
    onde = []
    for genero in lemas_diferentes:
        if 'UDPIPE24r' in lemas_diferentes[genero] and token['lema'] in lemas_diferentes[genero]['UDPIPE24r']:
            diverge += 1
            onde.append(genero)
    if diverge:
        if not 'UDPIPE24r' in analises_ambiguas:
            analises_ambiguas['UDPIPE24r'] = {}
        for _genero in onde:
            if not token['lema'] in analises_ambiguas['UDPIPE24r']:
                analises_ambiguas['UDPIPE24r'][token['lema']] = {}
            analises_ambiguas['UDPIPE24r'][token['lema']][_genero] = lemas_diferentes[_genero]['UDPIPE24r'][token['lema']]
            
for token in STANZA_acertos_PROP:
    o = int(token.split("<delimitador>")[0])
    s = int(token.split("<delimitador>")[1])
    t = int(token.split("<delimitador>")[2])
    token = STANZA_obras[o]['sentences'][s][t]
    diverge = -1
    onde = []
    for genero in lemas_diferentes:
        if 'STANZA' in lemas_diferentes[genero] and token['lema'] in lemas_diferentes[genero]['STANZA']:
            diverge += 1
            onde.append(genero)
    if diverge:
        if not 'STANZA' in analises_ambiguas:
            analises_ambiguas['STANZA'] = {}
        for _genero in onde:
            if not token['lema'] in analises_ambiguas['STANZA']:
                analises_ambiguas['STANZA'][token['lema']] = {}
            analises_ambiguas['STANZA'][token['lema']][_genero] = lemas_diferentes[_genero]['STANZA'][token['lema']]

### Distribuição de erros por sistema & gênero

In [54]:
gender_errors = {}
for combination in errors_distribution:
    if combination != "NENHUM":
        for erro in errors_distribution[combination]:
            o = int(erro.split("<delimitador>")[0])
            s = int(erro.split("<delimitador>")[1])
            t = int(erro.split("<delimitador>")[2])
            gender_golden = OBRAS_obras[o]['sentences'][s][t]['genero']
            for sistema in combination.split("|"):
                if sistema == "PALAVRAS":
                    gender_sistema = PALAVRAS_obras[o]['sentences'][s][t]['genero']
                elif sistema == "UDPIPE24r":
                    gender_sistema = UDPIPE24r_obras[o]['sentences'][s][t]['genero']
                elif sistema == "STANZA":
                    gender_sistema = STANZA_obras[o]['sentences'][s][t]['genero']
                if not gender_golden + "|" + gender_sistema in gender_errors:
                    gender_errors[gender_golden + "|" + gender_sistema] = []
                gender_errors[gender_golden + "|" + gender_sistema].append(erro)

# Testes 11/05/2020

In [ ]:
lista_sofias = {}
for obra in OBRAS_obras:
    for sentence in obra['sentences']:
        for token in sentence:
            if token['lema'] == "Robino":
                if not token['genero'] in lista_sofias:
                    lista_sofias[token['genero']] = 0
                lista_sofias[token['genero']] += 1
print(lista_sofias)

In [ ]:
import pprint
print([x for x in SEG_OBRAS if x.split("<delimitador>")[0] == "0" and x.split("<delimitador>")[1] == "8"])
#pprint.pprint(OBRAS_obras[0]['sentences'][8])

### HTML

In [24]:
import random
def randomly(seq):
    shuffled = list(seq)
    random.shuffle(shuffled)
    return iter(shuffled)

In [58]:
from datetime import datetime


html = "<style>body { width:40%; margin:auto; padding-top:10px; } td, th { padding:5px; } table { margin:auto; }</style>"
html += "<title>Comparação entre a anotação de nomes próprios de PESSOA no OBras realizada pelo PALAVRAS, pelo UDPipe e Stanza</title>"
html += '''<script>
function toggleDisplay(object) {
  var x = document.getElementById(object);
  if (x.style.display === "none") {
    x.style.display = "block";
  } else {
    x.style.display = "none";
  }
} 
</script>
'''
html += "<h1>Comparação entre a anotação de nomes próprios de PESSOA no OBras realizada pelo PALAVRAS, pelo UDPipe e Stanza</h1><hr>"

html += "<h2>(1) Descrição dos corpora</h2><table border='1'>"
html += "<tr><th>Características</th><th>PALAVRAS</th><th>UDPIPE24r</th><th>STANZA</th><th>GOLDEN</th></td></tr>"
html += "<tr><th>Obras</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    len(PALAVRAS_obras), 
    len(UDPIPE24r_obras), 
    len(STANZA_obras),
    len(OBRAS_obras)
)
html += "<tr><th>Sentenças</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    sum([len(x['sentences']) for x in PALAVRAS_obras]), 
    sum([len(x['sentences']) for x in UDPIPE24r_obras]), 
    sum([len(x['sentences']) for x in STANZA_obras]),
    sum([len(x['sentences']) for x in OBRAS_obras])
)
html += "<tr><th>Tokens</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    sum([len(x) for y in PALAVRAS_obras for x in y['sentences']]), 
    sum([len(x) for y in UDPIPE24r_obras for x in y['sentences']]), 
    sum([len(x) for y in STANZA_obras for x in y['sentences']]),
    sum([len(x) for y in OBRAS_obras for x in y['sentences']])
)
html += "<tr><th>Nomes próprios (compostos ou não)</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    len(SEG_PALAVRAS), 
    len(SEG_UDPIPE24r), 
    len(SEG_STANZA),
    f"{len(PROPN_OBRAS)} ({len(SEG_OBRAS)} são Pessoa ou hum)"
)
html += "</table>"

html += "<br><h2>(2) Desempenho na segmentação/identificação de nome próprio de PESSOA</h2><table border='1'>"
html += "<tr><th></th><th>PALAVRAS</th><th>UDPIPE24r</th><th>STANZA</th><th>GOLDEN</th></tr>"
html += "<tr><th>Acertos de nome próprio de PESSOA/segmentação</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    f"{round((len(PALAVRAS_acertos_PROP)/len(SEG_OBRAS))*100)}% ({len(PALAVRAS_acertos_PROP)})", 
    f"{round((len(UDPIPE24r_acertos_PROP)/len(SEG_OBRAS))*100)}% ({len(UDPIPE24r_acertos_PROP)})", 
    f"{round((len(STANZA_acertos_PROP)/len(SEG_OBRAS))*100)}% ({len(STANZA_acertos_PROP)})",
    str(len(SEG_OBRAS)) + " (100%)"
)
html += "</table>"

html += "<br><h2>(2.1) Caracterização dos nomes próprios de PESSOA</h2><table border='1'>"
html += "<tr><th></th><th>PALAVRAS</th><th>UDPIPE24r</th><th>STANZA</th><th>GOLDEN</th></tr>"
html += "<tr><th>Nome próprio simples</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    f'{len([x for x in PALAVRAS_acertos_PROP if not "=" in PALAVRAS_obras[int(x.split("<delimitador>")[0])]["sentences"][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]["lema"]])}',
    f'{len([x for x in UDPIPE24r_acertos_PROP if not "=" in UDPIPE24r_obras[int(x.split("<delimitador>")[0])]["sentences"][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]["lema"]])}',
    f'{len([x for x in STANZA_acertos_PROP if not "=" in STANZA_obras[int(x.split("<delimitador>")[0])]["sentences"][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]["lema"]])}',
    f'{len([x for x in SEG_OBRAS if not "=" in OBRAS_obras[int(x.split("<delimitador>")[0])]["sentences"][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]["lema"]])}',

)
html += "<tr><th>Nome próprio composto</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    f'{len([x for x in PALAVRAS_acertos_PROP if "=" in PALAVRAS_obras[int(x.split("<delimitador>")[0])]["sentences"][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]["lema"]])}',
    f'{len([x for x in UDPIPE24r_acertos_PROP if "=" in UDPIPE24r_obras[int(x.split("<delimitador>")[0])]["sentences"][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]["lema"]])}',
    f'{len([x for x in STANZA_acertos_PROP if "=" in STANZA_obras[int(x.split("<delimitador>")[0])]["sentences"][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]["lema"]])}',
    f'{len([x for x in SEG_OBRAS if "=" in OBRAS_obras[int(x.split("<delimitador>")[0])]["sentences"][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]["lema"]])}',
)
html += "<tr><th>Nomes próprios (compostos ou não) M</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    len([x for x in PALAVRAS_acertos_PROP if PALAVRAS_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "M"]),
    len([x for x in UDPIPE24r_acertos_PROP if UDPIPE24r_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "M"]),
    len([x for x in STANZA_acertos_PROP if STANZA_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "M"]),
    len([x for x in SEG_OBRAS if OBRAS_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "M"]),
)
html += "<tr><th>Nomes próprios (compostos ou não) F</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    len([x for x in PALAVRAS_acertos_PROP if PALAVRAS_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "F"]),
    len([x for x in UDPIPE24r_acertos_PROP if UDPIPE24r_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "F"]),
    len([x for x in STANZA_acertos_PROP if STANZA_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "F"]),
    len([x for x in SEG_OBRAS if OBRAS_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "F"]),
)
html += "<tr><th>Nomes próprios (compostos ou não) M/F</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    len([x for x in PALAVRAS_acertos_PROP if PALAVRAS_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "M/F"]),
    len([x for x in UDPIPE24r_acertos_PROP if UDPIPE24r_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "M/F"]),
    len([x for x in STANZA_acertos_PROP if STANZA_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "M/F"]),
    len([x for x in SEG_OBRAS if OBRAS_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "M/F"]),
)
html += "<tr><th>Nomes próprios (compostos ou não) 0</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    len([x for x in PALAVRAS_acertos_PROP if PALAVRAS_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "0"]),
    len([x for x in UDPIPE24r_acertos_PROP if UDPIPE24r_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "0"]),
    len([x for x in STANZA_acertos_PROP if STANZA_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "0"]),
    len([x for x in SEG_OBRAS if OBRAS_obras[int(x.split("<delimitador>")[0])]['sentences'][int(x.split("<delimitador>")[1])][int(x.split("<delimitador>")[2])]['genero'] == "0"]),
)

for genero in lemas_diferentes:
    html += "<tr><th>{}</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    f"Lemas diferentes {genero}",
    f'{len(lemas_diferentes[genero]["PALAVRAS"]) if "PALAVRAS" in lemas_diferentes[genero] else "0"}',
    f'{len(lemas_diferentes[genero]["UDPIPE24r"]) if "UDPIPE24r" in lemas_diferentes[genero] else "0"}',
    f'{len(lemas_diferentes[genero]["STANZA"]) if "STANZA" in lemas_diferentes[genero] else "0"}',
    f'{len(lemas_diferentes[genero]["OBRAS"]) if "OBRAS" in lemas_diferentes[genero] else "0"}',
)

for gram in distribution_ngrams:
    html += "<tr><th>{}</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    f"{gram}-grama",
    f'{distribution_ngrams[gram]["PALAVRAS"] if "PALAVRAS" in distribution_ngrams[gram] else "0"}',
    f'{distribution_ngrams[gram]["UDPIPE24r"] if "UDPIPE24r" in distribution_ngrams[gram] else "0"}',
    f'{distribution_ngrams[gram]["STANZA"] if "STANZA" in distribution_ngrams[gram] else "0"}',
    f'{distribution_ngrams[gram]["OBRAS"] if "OBRAS" in distribution_ngrams[gram] else "0"}',
)
html += "</table>"

for s, sistema in enumerate(analises_ambiguas):
    html += f"<br><h2><a style='cursor:pointer' onclick='toggleDisplay(\"{sistema}\");'>(2.2.{s+1}) Análises de gênero divergentes em {sistema} ({len(analises_ambiguas[sistema])} lemas)</a></h2><table id='{sistema}' style='display:none' border='1'>"
    html += "<tr><th></th><th>M</th><th>F</th><th>M/F</th><th>0</th></tr>"
    for lema in sorted(analises_ambiguas[sistema], key=lambda x: x):
        html += "<tr><td>{}</td><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
        lema,
        analises_ambiguas[sistema][lema]['M'] if 'M' in analises_ambiguas[sistema][lema] else "0",
        analises_ambiguas[sistema][lema]['F'] if 'F' in analises_ambiguas[sistema][lema] else "0",
        analises_ambiguas[sistema][lema]['M/F'] if 'M/F' in analises_ambiguas[sistema][lema] else "0",
        analises_ambiguas[sistema][lema]['0'] if '0' in analises_ambiguas[sistema][lema] else "0",
        )
    html += "</table>"

html += "<br><h2>(3a) Anotação de gênero em todos os sistemas ao mesmo tempo</h2><table border='1'>"
html += "<tr><th></th><th>PALAVRAS</th><th>UDPIPE24r</th><th>STANZA</th><th>Nomes próprios de PESSOA/segmentação que todos os sistemas acertaram</th></tr>"
html += "<tr><th>Acertos de gênero</th><td>{}</td><td>{}</td><td>{}</td><td>{}</td></tr>".format(
    f"{round((acertoGenero_PALAVRAS_total/nomes_comparaveis_todos)*100)}% ({acertoGenero_PALAVRAS_total})", 
    f"{round((acertoGenero_UDPIPE24r_total/nomes_comparaveis_todos)*100)}% ({acertoGenero_UDPIPE24r_total})", 
    f"{round((acertoGenero_STANZA_total/nomes_comparaveis_todos)*100)}% ({acertoGenero_STANZA_total})", 
    str(nomes_comparaveis_todos) + " (100%)"
)
html += "</table><br>"

html += "<br><h2>(3b) Desempenho de cada sistema individualmente</h2><table border='1'>"
html += "<tr><th></th><th>PALAVRAS</th><th>Nomes próprios de PESSOA/segmentação que acertou</th></tr>"
html += "<tr><th>Acertos de gênero</th><td>{}</td><td>{}</td></tr>".format(
    f"{round((acertoGenero_PALAVRAS/nomes_comparaveis_PALAVRAS)*100)}% ({acertoGenero_PALAVRAS})", 
    str(nomes_comparaveis_PALAVRAS) + " (100%)"
)
html += "</table><br>"

html += "<br><table border='1'>"
html += "<tr><th></th><th>UDPIPE24r</th><th>Nomes próprios de PESSOA/segmentação que acertou</th></tr>"
html += "<tr><th>Acertos de gênero</th><td>{}</td><td>{}</td></tr>".format(
    f"{round((acertoGenero_UDPIPE24r/nomes_comparaveis_UDPIPE24r)*100)}% ({acertoGenero_UDPIPE24r})", 
    str(nomes_comparaveis_UDPIPE24r) + " (100%)"
)
html += "</table><br>"

html += "<br><table border='1'>"
html += "<tr><th></th><th>STANZA</th><th>Nomes próprios de PESSOA/segmentação que acertou</th></tr>"
html += "<tr><th>Acertos de gênero</th><td>{}</td><td>{}</td></tr>".format(
    f"{round((acertoGenero_STANZA/nomes_comparaveis_STANZA)*100)}% ({acertoGenero_STANZA})", 
    str(nomes_comparaveis_STANZA) + " (100%)"
)
html += "</table>"

html += "<br><h2>(4a) Distribuição dos erros por sistema</h2>"
html += "<br><table border='1'>"
html += "<tr><th>Quem errou</th><th>Quantidade de erros</th></tr>"
for combination in errors_distribution:
    html += "<tr><td>{}</td><td>{}</td></tr>".format(
        combination.replace("|", " e "),
        len(errors_distribution[combination])
    )
html += "</table>"

html += "<br><h2>(4b) Distribuição dos erros por gênero</h2>"
html += "<br><table border='1'>"
html += "<tr><th>GOLDEN</th><th>SISTEMA</th><th>QUANTIDADE DE ERROS</th></tr>"
for combination in gender_errors:
    html += "<tr><td>{}</td><td>{}</td><td>{}</td></tr>".format(
        combination.split("|")[0],
        combination.split("|")[1],
        len(gender_errors[combination])
    )
html += "</table>"

html += "<br><h2>(5) Análise dos primeiros 20 casos + 200 casos aleatórios</h2>"

for i, token in enumerate(acerto_ambos):
    o = int(token.split("<delimitador>")[0])
    s = int(token.split("<delimitador>")[1])
    t = int(token.split("<delimitador>")[2])
    html += "<hr><table style='text-align:center'>"
    html += "<tr><td colspan='4'>{} / {}<br>{}</td></tr>".format(str(i+1), len(acerto_ambos), " ".join([x['forma'] for x in UDPIPE24r_obras[o]['sentences'][s]]).replace(UDPIPE24r_obras[o]['sentences'][s][t]['forma'], '<b>' + UDPIPE24r_obras[o]['sentences'][s][t]['forma'] + "</b>"))
    html += "<tr><th>PALAVRAS</th><th>UDPIPE24r</th><th>STANZA</th><th>GOLDEN</th></tr>"
    html += "<tr><td><font color='{cor_palavras}'>{}</font></td><td><font color='{cor_udpipe24r}'>{}</font></td><td><font color='{cor_stanza}'>{}</font></td><td>{}</td></tr>".format(
        PALAVRAS_obras[o]['sentences'][s][t]['genero'], 
        UDPIPE24r_obras[o]['sentences'][s][t]['genero'], 
        STANZA_obras[o]['sentences'][s][t]['genero'], 
        OBRAS_obras[o]['sentences'][s][t]['genero'], 
        cor_palavras="red" if PALAVRAS_obras[o]['sentences'][s][t]['genero'] != OBRAS_obras[o]['sentences'][s][t]['genero'] else "green", 
        cor_udpipe24r="red" if UDPIPE24r_obras[o]['sentences'][s][t]['genero'] != OBRAS_obras[o]['sentences'][s][t]['genero'] else "green", 
        cor_stanza="red" if STANZA_obras[o]['sentences'][s][t]['genero'] != OBRAS_obras[o]['sentences'][s][t]['genero'] else "green", 
    )
    html += "</table>"
    if i == 19:
        break
        
for i, token in enumerate(randomly(acerto_ambos)):
    o = int(token.split("<delimitador>")[0])
    s = int(token.split("<delimitador>")[1])
    t = int(token.split("<delimitador>")[2])
    html += "<hr><table style='text-align:center'>"
    html += "<tr><td colspan='4'>{} / {}<br>{}</td></tr>".format(str(i+1), len(acerto_ambos), " ".join([x['forma'] for x in UDPIPE24r_obras[o]['sentences'][s]]).replace(UDPIPE24r_obras[o]['sentences'][s][t]['forma'], '<b>' + UDPIPE24r_obras[o]['sentences'][s][t]['forma'] + "</b>"))
    html += "<tr><th>PALAVRAS</th><th>UDPIPE24r</th><th>STANZA</th><th>GOLDEN</th></tr>"
    html += "<tr><td><font color='{cor_palavras}'>{}</font></td><td><font color='{cor_udpipe24r}'>{}</font></td><td><font color='{cor_stanza}'>{}</font></td><td>{}</td></tr>".format(
        PALAVRAS_obras[o]['sentences'][s][t]['genero'], 
        UDPIPE24r_obras[o]['sentences'][s][t]['genero'], 
        STANZA_obras[o]['sentences'][s][t]['genero'], 
        OBRAS_obras[o]['sentences'][s][t]['genero'], 
        cor_palavras="red" if PALAVRAS_obras[o]['sentences'][s][t]['genero'] != OBRAS_obras[o]['sentences'][s][t]['genero'] else "green", 
        cor_udpipe24r="red" if UDPIPE24r_obras[o]['sentences'][s][t]['genero'] != OBRAS_obras[o]['sentences'][s][t]['genero'] else "green", 
        cor_stanza="red" if STANZA_obras[o]['sentences'][s][t]['genero'] != OBRAS_obras[o]['sentences'][s][t]['genero'] else "green", 
    )
    html += "</table>"
    if i == 199:
        break

html += "<br><hr>Relatório gerado em " + str(datetime.now()) + "<br><br>"

with open("gender-palavras-udpipe.html", "w") as f:
    f.write(html)